In [1]:
import torch
import pickle
import numpy as np
import pandas as pd
import os

from os.path import dirname



root_path = dirname(os.getcwd()) + "/HGNN_NA"

pd.set_option("display.max_columns", None)
data_dir = root_path + "/data/datasets/original/"
data_dir_processed = root_path + "/data/datasets/processed/"
data_dir_graphs = root_path + "/data/datasets/graphs/"

print(root_path, data_dir, data_dir_processed, data_dir_graphs, sep="\n")

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
# device = "cpu"

/home/sebdis/ProcessMining/HGNN/HGNN_NA
/home/sebdis/ProcessMining/HGNN/HGNN_NA/data/datasets/original/
/home/sebdis/ProcessMining/HGNN/HGNN_NA/data/datasets/processed/
/home/sebdis/ProcessMining/HGNN/HGNN_NA/data/datasets/graphs/


In [3]:
dataset = "Helpdesk"

In [5]:
categorical_columns = [
    "Activity"
]
real_value_columns = [
    "time:timestamp",
]

In [6]:
tab_all = pd.read_csv(data_dir_processed+dataset+"_processed_all.csv")
tab_all.head()

CaseID  Activity  time:timestamp
0       2         1       18.064921
1       2         8       18.064921
2       2         6       18.067402
3       3         1       17.033106
4       3         8       17.051399

In [7]:
import random

torch.manual_seed(0)
torch.cuda.manual_seed(0)
random.seed(0)
np.random.seed(0)

In [8]:
with open(data_dir_graphs + dataset + "_TRAIN_event_prediction_FINAL.pkl", "rb") as f:
    X_train = pickle.load(f)
with open(data_dir_graphs + dataset + "_VALID_event_prediction_FINAL.pkl", "rb") as f:
    X_valid = pickle.load(f)
with open(data_dir_graphs + dataset + "_TEST_event_prediction_FINAL.pkl", "rb") as f:
    X_test = pickle.load(f)

In [9]:

from torch_geometric.data import Dataset
from torch_geometric.loader import DataLoader
from torch_geometric.transforms import ToUndirected, NormalizeFeatures

transform = ToUndirected()

with torch.no_grad():
        for i in range(len(X_train)):
                X_train[i] = transform(X_train[i])
        for i in range(len(X_valid)):
                X_valid[i] = transform(X_valid[i])
        for i in range(len(X_test)):
                X_test[i] = transform(X_test[i])
    






In [10]:
edge_types = set()
node_types = set()
for i in range(len(X_train)):
    n, edge_type = X_train[i].metadata()
    for x in n:
        node_types.add(x)
    for x in edge_type:
        edge_types.add(x)
for i in range(len(X_valid)):
    n, edge_type = X_valid[i].metadata()
    for x in n:
        node_types.add(x)
    for x in edge_type:
        edge_types.add(x)
for i in range(len(X_test)):
    n, edge_type = X_test[i].metadata()
    for x in n:
        node_types.add(x)
    for x in edge_type:
        edge_types.add(x)



In [11]:
node_types = list(node_types)
edge_types = list(edge_types)

In [12]:
node_types

['Activity', 'time:timestamp']

In [13]:
edge_types

[('time:timestamp', 'rev_related_to', 'Activity'),
 ('Activity', 'related_to', 'time:timestamp'),
 ('Activity', 'followed_by', 'Activity'),
 ('time:timestamp', 'related_to', 'time:timestamp')]

In [14]:
def get_weights(load, key):
    weights = []
    
    cl_train = [0 for _ in tab_all[key].unique()]
    
    print(cl_train)
    
    for i,x in enumerate(load):

        
        classes = x.y[key]

        # print(classes)
        
        for c in list(classes):
            try:
                cl_train[c] +=1
            except KeyError:
                cl_train[c] = 1
    s = sum(cl_train)
    
    print(cl_train)
    
    weights = [s/x if x > 0 else 0 for x in cl_train]

    # weights = [0.7,0.7,1,0.7,0.7,0.7,0.7,0.7,0.7,0.7]
    weights = torch.tensor(weights, device=device)
    print(weights)
    return weights
    

In [16]:
edge_features_dims = {}

for i in range(len(X_train)):
    for k in X_train[i].edge_attr_dict.keys():
        edge_features_dims[k] = X_train[i].edge_attr_dict[k].shape[1]
for i in range(len(X_valid)):
    for k in X_valid[i].edge_attr_dict.keys():
        edge_features_dims[k] = X_valid[i].edge_attr_dict[k].shape[1]
for i in range(len(X_test)):
    for k in X_test[i].edge_attr_dict.keys():
        edge_features_dims[k] = X_test[i].edge_attr_dict[k].shape[1]

edge_features_dims

{('Activity', 'followed_by', 'Activity'): 2,
 ('time:timestamp', 'related_to', 'time:timestamp'): 2}

In [17]:
act_weights = get_weights(DataLoader(X_train, batch_size=1024, shuffle=False), "Activity")
# res_roles_weights = get_weights(DataLoader(X_train, batch_size=1024, shuffle=False), "org:resource:role")


[0, 0, 0, 0, 0, 0, 0, 0, 0]
[53, 32, 0, 0, 1, 2164, 4, 1035, 558]
tensor([7.2585e+01, 1.2022e+02, 0.0000e+00, 0.0000e+00, 3.8470e+03, 1.7777e+00,
        9.6175e+02, 3.7169e+00, 6.8943e+00], device='cuda:0')


## Hyperopt

In [19]:
from ax.service.managed_loop import optimize

In [20]:
from torch_geometric.nn import (
    HeteroConv,
    global_mean_pool,
    GATv2Conv
)
from torch.nn import (
    ModuleList,
    Module,
    Linear
  )
from typing_extensions import Self

In [21]:
class HGNN(Module):

    def __init__(self, output_cat, output_real,nodes_relations, relations_with_features, parameters) -> Self:  # type: ignore
        super().__init__()

        # List of convolutional layers
        
        hid = parameters["hid"]
        layers = parameters["layers"]
        aggregation = parameters["aggregation"]
        n_heads = parameters["heads"]
        
        self.output_cat = output_cat
        self.output_real = output_real
        
        self.convs = ModuleList()
        for _ in range(layers):
            conv = HeteroConv(
                {
                    relation: (
                        GATv2Conv((-1,-1), add_self_loops=False, out_channels=hid, heads=n_heads, concat=False)
                        if relation not in relations_with_features
                        else GATv2Conv((-1,-1), add_self_loops=False, out_channels=hid,heads=n_heads, edge_dim=relations_with_features[relation], concat=False)
                    )
                    for relation in nodes_relations
                },
                aggr=aggregation,
            )

            self.convs.append(conv)

        self.FC = {}
        
        for k in output_cat:
            self.FC[k] = Linear(hid, output_cat[k], device=device)
        for k in output_real:
            self.FC[k] = Linear(hid, 1, device=device)
        
    
        
        

    def forward(self, batch):

        for i in range(len(self.convs)):
            batch.x_dict = self.convs[i]( 
                batch.x_dict, batch.edge_index_dict, batch.edge_attr_dict
            )

            batch.x_dict = {key: x.relu() for key, x in batch.x_dict.items()}


        output = {}
        
        for k in self.output_cat:
            output[k] = global_mean_pool(batch.x_dict[k], batch[k].batch)
            output[k] = self.FC[k](output[k])
        for k in self.output_real:
            output[k] = global_mean_pool(batch.x_dict[k], batch[k].batch)
            output[k] = self.FC[k](output[k]).reshape(1,-1)[0]
            

        return output

In [22]:
from torcheval.metrics.functional import multiclass_accuracy, multiclass_f1_score

In [23]:
import torch.nn as nn

In [24]:
import time

In [26]:
from copy import deepcopy


def train_hgnn(config, output_cat, output_real, epochs=15):
    print(config)

    net = HGNN(
        parameters=config,
        output_cat=output_cat,
        output_real=output_real,
        nodes_relations=edge_types,
        relations_with_features=edge_features_dims,
    )
    net = net.to(device)

    losses = {}

    for k in output_cat:
        losses[k] = (
            nn.CrossEntropyLoss()
            if k != "Activity"
            else nn.CrossEntropyLoss(act_weights)
        )
    for k in output_real:
        losses[k] = nn.L1Loss()

    train_loader = DataLoader(X_train, batch_size=config["batch_size"], shuffle=True)
    valid_loader = DataLoader(X_valid, batch_size=config["batch_size"], shuffle=True)

    optimizer = torch.optim.Adam(net.parameters(), lr=config["lr"])

    best_model = None
    best_loss = 0
    patience = 20
    pat_count = 0

    torch.cuda.empty_cache()

    for epoch in range(0, epochs):
        start_time = time.time()

        print(f"Epoch: {epoch}\n")

        net.train()
        for _, x in enumerate(train_loader):
            x = x.to(device)

            labels = x.y

            optimizer.zero_grad()
            outputs = net(x)

            losses_step = {k: losses[k](outputs[k], labels[k]) for k in losses}

            total_loss = 0
            for k in losses_step:
                total_loss += losses_step[k]

            total_loss.backward()
            optimizer.step()

        predictions_categorical = {k: [] for k in output_cat}
        target_categorical = {k: [] for k in output_cat}

        avg_MAE = {k: [] for k in output_real}

        running_total_loss = []

        net.eval()
        with torch.no_grad():
            for i, x in enumerate(valid_loader):
                x = x.to(device)

                labels = x.y

                outputs = net(x)

                losses_step = {k: losses[k](outputs[k], labels[k]) for k in losses}

                running_total_loss.append(sum(list(losses_step.values())))

                for k in output_cat:
                    predictions_categorical[k].append(
                        torch.argmax(torch.softmax(outputs[k], dim=1), 1)
                    )
                    target_categorical[k].append(labels[k])

                for k in output_real:
                    avg_MAE[k].append(losses_step[k])

        for k in predictions_categorical:
            predictions_categorical[k] = torch.cat(predictions_categorical[k])
            target_categorical[k] = torch.cat(target_categorical[k])

        macro_f1_activity = multiclass_f1_score(
            predictions_categorical["Activity"],
            target_categorical["Activity"],
            num_classes=output_cat["Activity"],
            average="macro",
        )

        accuracy = {
            k: multiclass_accuracy(
                predictions_categorical[k],
                target_categorical[k],
                num_classes=output_cat[k],
            )
            for k in output_cat
        }

        avg_MAE = {k: sum(avg_MAE[k]) / len(avg_MAE[k]) for k in avg_MAE}

        val_loss = sum(running_total_loss) / len(running_total_loss)

        print(f"\nVALIDATION")
        for k in accuracy:
            (
                print("{}: acc {:.4f}".format(k, accuracy[k]))
                if k != "Activity"
                else print(
                    "{}: acc {:.4f} macroF1 {:.4f}".format(
                        k, accuracy[k], macro_f1_activity.item()
                    )
                )
            )
        for k in avg_MAE:
            print("{}: MAE {:.4f}".format(k, avg_MAE[k]))
        print("TOTAL_LOSS: {:.4f}".format(val_loss))
        print("epoch time {}s\n".format(time.time() - start_time))

        if epoch == 0:
            best_model = deepcopy(net)
            best_loss = val_loss
        else:
            if val_loss < best_loss:
                best_loss = val_loss
                best_model = deepcopy(net)
                pat_count = 0
                print("new best model found")
            if pat_count == patience:
                print(
                    "Validation performance didn't improve for {} epochs. Training stops.".format(
                        pat_count
                    )
                )
                return best_model
        pat_count += 1

    return best_model

In [28]:
def test_hgnn(net, output_cat, output_real):
    test_loader = DataLoader(X_train, batch_size=128, shuffle=False)
    
    losses = {}
    
    for k in output_cat:
        losses[k] = (
            nn.CrossEntropyLoss()
            if k != "Activity"
            else nn.CrossEntropyLoss(act_weights)
        )
    for k in output_real:
        losses[k] = nn.L1Loss()
    
    
    
    
    
    predictions_categorical = {k: [] for k in output_cat}
    target_categorical = {k: [] for k in output_cat}

    avg_MAE = {k : [] for k in output_real}
    
    total_loss = []
        
    net.eval()
    with torch.no_grad():
        for i, x in enumerate(test_loader):
            x = x.to(device)
            
            labels = x.y
            
            outputs = net(x)
            
     
            losses_step = {k: losses[k](outputs[k], labels[k]).item() for k in losses}
            total_loss.append(sum(list(losses_step.values())))
            
            for k in output_cat:
                    predictions_categorical[k].append(
                        torch.argmax(torch.softmax(outputs[k], dim=1), 1)
                    )
                    target_categorical[k].append(labels[k])
            
            
            for k in output_real:
                    avg_MAE[k].append(losses_step[k])
                    
    for k in predictions_categorical:
            predictions_categorical[k] = torch.cat(predictions_categorical[k])
            target_categorical[k] = torch.cat(target_categorical[k])
               
            
    macro_f1_activity = multiclass_f1_score(
            predictions_categorical["Activity"],
            target_categorical["Activity"],
            num_classes=output_cat["Activity"],
            average="macro",
        )
            
    accuracy = {
            k: multiclass_accuracy(
                predictions_categorical[k],
                target_categorical[k],
                num_classes=output_cat[k],
            )
            for k in output_cat
        }
    
   
    
    avg_MAE = {k : sum(avg_MAE[k]) / len(avg_MAE[k]) for k in avg_MAE}
    
    
    Average_total_loss = sum(total_loss) / len(total_loss)
    
    res = {f"{k}_acc" : accuracy[k].item() for k in accuracy}  | {"MacroF1Act" : macro_f1_activity.item()} | {f"{k}_mae" : avg_MAE[k] for k in avg_MAE} | {"AVG_total_loss" : Average_total_loss} 
    
    print(res)
    
    return res

In [29]:
list_unique = {k : list(tab_all[k].unique()) for k in categorical_columns}
list_unique

{'Activity': [1, 8, 6, 3, 9, 2, 4, 5, 7]}

In [30]:
outputcat = {k : len(list_unique[k]) if len(list_unique[k]) > 1 else None for k in list_unique}
outputcat = {k : v for k,v in outputcat.items() if v != None}
outputreal = real_value_columns
print(outputcat)
print(outputreal)

{'Activity': 9}
['time:timestamp']


In [31]:
def train_evaluate(config):
    trained_net = train_hgnn(config, output_cat=outputcat, output_real=outputreal, epochs = 100)
    return test_hgnn(trained_net, output_cat=outputcat, output_real=outputreal)

In [32]:
config = {'lr': 0.005059480954002739, 'batch_size': 256, 'heads': 1, 'hid': 128, 'layers': 2, 'aggregation': 'max'}

In [33]:
train_evaluate(config)

{'lr': 0.005059480954002739, 'batch_size': 256, 'heads': 1, 'hid': 128, 'layers': 2, 'aggregation': 'max'}
Epoch: 0




VALIDATION
Activity: acc 0.7531 macroF1 0.1432
time:timestamp: MAE 0.9094
TOTAL_LOSS: 3.4216
epoch time 1.195756196975708s

Epoch: 1




VALIDATION
Activity: acc 0.7531 macroF1 0.1432
time:timestamp: MAE 1.1734
TOTAL_LOSS: 3.3887
epoch time 1.0484428405761719s

new best model found
Epoch: 2




VALIDATION
Activity: acc 0.7531 macroF1 0.1432
time:timestamp: MAE 0.3156
TOTAL_LOSS: 3.0609
epoch time 0.9934322834014893s

new best model found
Epoch: 3




VALIDATION
Activity: acc 0.7562 macroF1 0.1948
time:timestamp: MAE 0.1144
TOTAL_LOSS: 1.7751
epoch time 0.9412002563476562s

new best model found
Epoch: 4



...


VALIDATION
Activity: acc 0.5540 macroF1 0.1737
time:timestamp: MAE 0.2927
TOTAL_LOSS: 2.5882
epoch time 0.8276379108428955s

Epoch: 25




VALIDATION
Activity: acc 0.1883 macroF1 0.1188
time:timestamp: MAE 0.3032
TOTAL_LOSS: 2.6255
epoch time 0.8430221080780029s

Epoch: 26




VALIDATION
Activity: acc 0.1821 macroF1 0.1199
time:timestamp: MAE 0.1225
TOTAL_LOSS: 2.3366
epoch time 0.8406431674957275s

Validation performance didn't improve for 20 epochs. Training stops.


{'Activity_acc': 0.17806082963943481, 'MacroF1Act': 0.09799403697252274, 'time:timestamp_mae': 0.12321199981435653, 'AVG_total_loss': 1.6481174276240411}


{'Activity_acc': 0.17806082963943481,
 'MacroF1Act': 0.09799403697252274,
 'time:timestamp_mae': 0.12321199981435653,
 'AVG_total_loss': 1.6481174276240411}

In [35]:
best_parameters, values, experiment, model = optimize(
    parameters=[
        {"name": "hid", "type": "choice", "values": [128], "value_type": "int", "is_ordered" : True,"sort_values":False},
        #{"name": "layers", "type": "choice", "values": [2, 3, 4, 5], "value_type": "int", "is_ordered" : True, "sort_values":False},
        {"name": "layers", "type": "choice", "values": [2], "value_type": "int", "is_ordered" : True, "sort_values":False},
        {"name": "lr", "type": "range", "bounds": [1e-4, 1e-1], "value_type": "float", "log_scale": True},
        {"name": "batch_size", "type": "choice", "values": [128, 256, 512], "value_type": "int", "is_ordered" : True,"sort_values":False}, 
        {"name": "heads", "type": "choice", "values": [1,2], "value_type": "int", "is_ordered" : True,"sort_values":False},
        #{"name": "heads", "type": "choice", "values": [1], "value_type": "int", "is_ordered" : True,"sort_values":False},
        
        #{"name": "aggregation", "type" : "choice", "values" :["sum", "mean", "max"], "value_type" : "str"}
        {"name": "aggregation", "type" : "choice", "values" :["max"], "value_type" : "str"},
     
    ],
  
    evaluation_function=train_evaluate,
    objective_name='AVG_total_loss',
    arms_per_trial=1,
    minimize = True,
    random_seed = 123,
    total_trials = 100
)

print(best_parameters)
means, covariances = values
print(means)
print(experiment)

[INFO 01-14 15:13:49] ax.service.utils.instantiation: Choice parameter hid contains only one value, converting to a fixed parameter instead.
[INFO 01-14 15:13:49] ax.service.utils.instantiation: Choice parameter layers contains only one value, converting to a fixed parameter instead.
[INFO 01-14 15:13:49] ax.service.utils.instantiation: Choice parameter aggregation contains only one value, converting to a fixed parameter instead.
[INFO 01-14 15:13:49] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[FixedParameter(name='hid', parameter_type=INT, value=128), FixedParameter(name='layers', parameter_type=INT, value=2), RangeParameter(name='lr', parameter_type=FLOAT, range=[0.0001, 0.1], log_scale=True), ChoiceParameter(name='batch_size', parameter_type=INT, values=[128, 256, 512], is_ordered=True, sort_values=False), ChoiceParameter(name='heads', parameter_type=INT, values=[1, 2], is_ordered=True, sort_values=False), FixedParameter(name='aggregation', paramete

{'lr': 0.0001865322718407359, 'batch_size': 256, 'heads': 1, 'hid': 128, 'layers': 2, 'aggregation': 'max'}
Epoch: 0




VALIDATION
Activity: acc 0.0694 macroF1 0.0216
time:timestamp: MAE 16.4027
TOTAL_LOSS: 19.1967
epoch time 0.9223380088806152s

Epoch: 1




VALIDATION
Activity: acc 0.1667 macroF1 0.0476
time:timestamp: MAE 14.6643
TOTAL_LOSS: 17.1878
epoch time 0.8962159156799316s

new best model found
Epoch: 2




VALIDATION
Activity: acc 0.1667 macroF1 0.0476
time:timestamp: MAE 13.0101
TOTAL_LOSS: 15.3800
epoch time 1.0126864910125732s

new best model found
Epoch: 3



...


VALIDATION
Activity: acc 0.5386 macroF1 0.2009
time:timestamp: MAE 0.0389
TOTAL_LOSS: 1.8362
epoch time 1.2039835453033447s

Validation performance didn't improve for 20 epochs. Training stops.


[INFO 01-14 16:46:33] ax.core.experiment: Attached data has some metrics ({'Activity_acc', 'MacroF1Act', 'time:timestamp_mae'}) that are not among the metrics on this experiment. Note that attaching data will not automatically add those metrics to the experiment. For these metrics to be automatically fetched by `experiment.fetch_data`, add them via `experiment.add_tracking_metric` or update the experiment's optimization config.
[ERROR 01-14 16:46:33] ax.core.observation: Data contains metric Activity_acc that has not been added to the experiment. You can either update the `optimization_config` or attach it as a tracking metric using `Experiment.add_tracking_metrics` or `AxClient.add_tracking_metrics`. Ignoring all data for metric Activity_acc.
NoneType: None
[ERROR 01-14 16:46:33] ax.core.observation: Data contains metric MacroF1Act that has not been added to the experiment. You can either update the `optimization_config` or attach it as a tracking metric using `Experiment.add_tracking

{'Activity_acc': 0.4697166681289673, 'MacroF1Act': 0.2538028955459595, 'time:timestamp_mae': 0.03967870324249229, 'AVG_total_loss': 1.2614246787984045}


[ERROR 01-14 16:46:33] ax.core.observation: Data contains metric Activity_acc that has not been added to the experiment. You can either update the `optimization_config` or attach it as a tracking metric using `Experiment.add_tracking_metrics` or `AxClient.add_tracking_metrics`. Ignoring all data for metric Activity_acc.
NoneType: None
[ERROR 01-14 16:46:33] ax.core.observation: Data contains metric MacroF1Act that has not been added to the experiment. You can either update the `optimization_config` or attach it as a tracking metric using `Experiment.add_tracking_metrics` or `AxClient.add_tracking_metrics`. Ignoring all data for metric MacroF1Act.
NoneType: None
[ERROR 01-14 16:46:33] ax.core.observation: Data contains metric time:timestamp_mae that has not been added to the experiment. You can either update the `optimization_config` or attach it as a tracking metric using `Experiment.add_tracking_metrics` or `AxClient.add_tracking_metrics`. Ignoring all data for metric time:timestamp_m

{'lr': 0.0012542372130208597, 'batch_size': 128, 'heads': 1, 'hid': 128, 'layers': 2, 'aggregation': 'max'}
{'AVG_total_loss': 1.3102757290953162}
Experiment(None)


In [36]:
from ax.service.utils.report_utils import exp_to_df

results = exp_to_df(experiment)

[WARNING 01-14 16:46:53] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [40]:
results.sort_values(by="MacroF1Act")

trial_index arm_name trial_status generation_method  AVG_total_loss  \
10           10     10_0    COMPLETED           BoTorch        1.998454   
2             2      2_0    COMPLETED             Sobol        1.894153   
70           70     70_0    COMPLETED           BoTorch        1.594455   
77           77     77_0    COMPLETED           BoTorch        1.420604   
35           35     35_0    COMPLETED           BoTorch        1.409806   
..          ...      ...          ...               ...             ...   
25           25     25_0    COMPLETED           BoTorch        1.417493   
58           58     58_0    COMPLETED           BoTorch        1.239487   
54           54     54_0    COMPLETED           BoTorch        1.214505   
32           32     32_0    COMPLETED           BoTorch        1.570326   
95           95     95_0    COMPLETED           BoTorch        1.298225   

    Activity_acc  MacroF1Act  time:timestamp_mae        lr  batch_size  heads  \
10      0.188199    0.073564            0.124517  0.000164         512      2   
2       0.165844    0.127130            0.246068  0.007958         512      1   
70      0.243047    0.140852            0.162602  0.003989         256      2   
77      0.289576    0.156018            0.051033  0.001963         128      2   
35      0.234728    0.163568            0.039409  0.000899         512      1   
..           ...         ...                 ...       ...         ...    ...   
25      0.600208    0.277250            0.195704  0.012348         128      2   
58      0.663634    0.277399            0.061754  0.002098         128      1   
54      0.526124    0.283785            0.056398  0.001513         128      1   
32      0.517286    0.319382            0.184083  0.018814         256      2   
95      0.620224    0.355627            0.059117  0.001688         128      2   

    hid  layers aggregation  
10  128       2         max  
2   128       2         max  
70  128       2         max  
77  128       2         max  
35  128       2         max  
..  ...     ...         ...  
25  128       2         max  
58  128       2         max  
54  128       2         max  
32  128       2         max  
95  128       2         max  

[100 rows x 14 columns]

In [38]:
results = results.sort_values(by="AVG_total_loss")

In [39]:
results.to_csv("Helpdesk.csv", sep=",")